In [57]:
from numpy import *
from scipy.constants import hbar, e
from plotly.graph_objs import *
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode()

In [113]:
def s21(freqs, w0, kappa):
    return 1/(1-1j*(freqs-w0)/(kappa/2))

## Control and readout: The dispersive limit
Koch, 2007

In the dispersive limit, detunings $\Delta_i = \omega_{i, i+1} - \omega_r$ between transmon and cavity are large. In particular

$$
g_{01}/ |\Delta_0| << 1
$$

$$
g_{01}/ |\Delta_0 + \alpha|
$$

We can use an effective Hamiltonian

$$
\hat{H}_{eff}/\hbar = \frac{\omega'_{01}}{2}\hat{\sigma}_z + (\omega'_r + \chi\hat{\sigma}_z)\hat{a}^\dagger\hat{a}
$$

where primes indicate renormalizations due to interactions:

$$
\omega'_r = \omega_r - \chi_{12}/2
$$

$$
\omega'_{01} = \omega_{01} + \chi_{01}
$$


The effective dispersive shift $\chi$ is given by

$$
\chi = \chi_{01} - \chi_{12}/2
$$

where

$$
\chi_{ij} \equiv \frac{g^2_{ij}}{\omega_{ij} - \omega_r}
$$

and $\omega_{ij} = \omega_j - \omega_i$.

Plugging in, 

$$
\chi = \frac{g_{01}^2}{\omega_{01} - \omega_r} - \frac{g^2_{12}/2}{\omega_{12}-\omega_r}
$$

In [131]:
wr = 5e9 * 2 * pi #5GHz
w01 = 6e9 * 2 * pi #5.5GHz
print("wr = {} GHz".format(wr/(2*pi*1e9)))
print("w01 = {} GHz".format(w01/(2*pi*1e9)))

alpha = - 300e6 * 2 * pi #300MHz
w12 = alpha + w01
print("w12 = {} GHz".format(w12/(2*pi*1e9)))

delta = wr - w01
print("delta = {} GHz".format(delta/(2*pi*1e9)))

g = 100e6 * 2 * pi #100MHz

chi = g**2 / delta
print('chi = {} MHz'.format(chi/(2*pi*1e6)))


g01 = g * (sqrt(-2*alpha/(8*w01)))
g12 = sqrt(2) * g01
print('g01 = {} MHz'.format(g01/(2*pi*1e6)))
print('g12 = {} MHz'.format(g12/(2*pi*1e6)))

chi12 = g12**2 / 2 / (w12-wr)
wrp = wr - chi12/2
print("wr' = {} GHz".format(wrp/(2*pi*1e9)))

wr = 5.0 GHz
w01 = 5.999999999999999 GHz
w12 = 5.699999999999999 GHz
delta = -0.9999999999999997 GHz
chi = -10.000000000000002 MHz
g01 = 11.180339887498947 MHz
g12 = 15.811388300841895 MHz
wr' = 4.999910714285714 GHz


In [132]:
Chi = g01**2 / (w01 - wr) - g12**2 / 2 /(alpha + w01 - wr)
print('Dressed 0 - Dressed 1 Chi = {} MHz'.format(Chi/(2*pi*1e6)))

Dressed 0 - Dressed 1 Chi = -0.05357142857142866 MHz


In [133]:
freqs = linspace(wr - 25e6*2*pi, wr + 25e6*2*pi, 501)
kappa = 1e6*2*pi
data = []

## Bare Peak
data.append(Scatter(
    x=freqs/(2e9*pi),
    y=real(s21(freqs, wr, kappa)),
    name="Bare"
    ))

## Dispersive Shift
data.append(Scatter(
    x=freqs/(2e9*pi),
    y=real(s21(freqs, wrp, kappa)),
    name="Dispersed"
    ))

## 0 State
data.append(Scatter(
    x=freqs/(2e9*pi),
    y=real(s21(freqs, wrp+chi, kappa)),
    name="0"
    ))

## 1 State
data.append(Scatter(
    x=freqs/(2e9*pi),
    y=real(s21(freqs, wrp-chi, kappa)),
    name="1"
    ))

fig = Figure(data=data)
iplot(fig)

In [135]:
data = []
freqs = linspace(wrp - 25e6*2*pi, wrp + 25e6*2*pi, 501)

## 0 State
data.append(Scatter(
    x=freqs/(2e9*pi),
    y=real(s21(freqs, wr+chi, kappa)),
    name="0"
    ))

## 1 State
data.append(Scatter(
    x=freqs/(2e9*pi),
    y=real(s21(freqs, wr-chi, kappa)),
    name="1"
    ))

fig = Figure(data=data)
iplot(fig)

In [166]:
wr = 5e9 * 2 * pi #5GHz
alpha = - 300e6 * 2 * pi #300MHz
g = 100e6 * 2 * pi #100MHz
freqs = linspace(wrp - 25e6*2*pi, wrp + 25e6*2*pi, 1001)

def calcChiShift(w01):

    w12 = alpha + w01
    delta = wr - w01

    chi = g**2 / delta

    g01 = g * (sqrt(-2*alpha/(8*w01)))
    g12 = sqrt(2) * g01
    chi12 = g12**2 / 2 / (w12-wr)
    wrp = wr - chi12/2
    
    return real(s21(freqs, wrp + chi, kappa)) + real(s21(freqs, wrp-chi, kappa))

def calcDispShift(w01):

    w12 = alpha + w01
    delta = wr - w01

    chi = g**2 / delta

    g01 = g * (sqrt(-2*alpha/(8*w01)))
    g12 = sqrt(2) * g01
    chi12 = g12**2 / 2 / (w12-wr)
    wrp = wr - chi12/2
    
    return real(s21(freqs, wrp, kappa))   
    

trace = Scatter(x=freqs/(2e9*pi), y=calcDispShift(5.5e9*2*pi))
fig  = Figure(data=[trace])
iplot(fig)

In [167]:
z = []
energies = linspace(4.2, 7.2, 101)*2e9*pi

for w01 in energies:
    s = calcDispShift(w01)
    z.append(s)

In [168]:
trace = Heatmap(x=freqs/(2e9*pi), y=energies/2e9/pi, z=z)
fig=Figure(data=[trace])
iplot(fig)